# Reinforcement Learning control strategies for Electric Vehicles fleet Virtual Power Plants
Thesis based on the development of a RL agent that manages a VPP through EVs charging stations in an household environment. Main optimization objectives of the VPP are: Valley filling, peak shaving and zero resulting load over time. Main action performed to reach objectives are: storage of Renewable energy resources and power push in the grid at high demand times. The development of the Virtual Power Plant environment is based on the ELVIS (Electric Vehicles Infrastructure Simulator) open library from DAI-Labor: https://github.com/dailab/elvis The thesis code is currently available at: (https://github.com/francescomaldonato/RL_VPP_Thesis)

Author: Francesco Maldonato

## VPP simulator Notebook based on EVs arrival, with StableBaselines3 trained model (Recurrent PPO) [25 EVs per week test]

Installing required packages and dependencies

In [ ]:
%%capture
!pip install py-elvis==0.2.1
!pip install pyyaml==5.4
!pip install plotly==5.9.0
!pip install -U kaleido==0.2.1

!pip install stable-baselines3[extra]==1.6.1
!pip install stable-baselines==1.6.1
!pip install sb3-contrib==1.6.1
!pip install gym==0.20.0
!pip install -q wandb==0.13.4

In [ ]:
#Cloning repository and changing directory
!git clone https://github.com/francescomaldonato/RL_VPP_Thesis.git
%cd RL_VPP_Thesis/
%ls

In [ ]:
import yaml
import numpy as np
from gym import Env
from VPP_environment import VPPEnv, VPP_Scenario_config
from elvis.config import ScenarioConfig
import os
import torch
import random
import wandb
from sb3_contrib import RecurrentPPO #The available algoritmhs in sb3-contrib for the custom environment with MultiInputPolicy
from sb3_contrib.common.maskable.utils import get_action_masks
import stable_baselines3 as sb3
from stable_baselines3.common.env_checker import check_env

#Check if cuda device is available for training
print("Torch-Cuda available device:", torch.cuda.is_available())
print(sb3.get_system_info())
#!wandb --version

Torch-Cuda available device: False
OS: Linux-5.10.133+-x86_64-with-Ubuntu-18.04-bionic #1 SMP Fri Aug 26 08:44:51 UTC 2022
Python: 3.7.14
Stable-Baselines3: 1.6.1
PyTorch: 1.12.1+cu113
GPU Enabled: False
Numpy: 1.21.6
Gym: 0.20.0

({'OS': 'Linux-5.10.133+-x86_64-with-Ubuntu-18.04-bionic #1 SMP Fri Aug 26 08:44:51 UTC 2022', 'Python': '3.7.14', 'Stable-Baselines3': '1.6.1', 'PyTorch': '1.12.1+cu113', 'GPU Enabled': 'False', 'Numpy': '1.21.6', 'Gym': '0.20.0'}, 'OS: Linux-5.10.133+-x86_64-with-Ubuntu-18.04-bionic #1 SMP Fri Aug 26 08:44:51 UTC 2022\nPython: 3.7.14\nStable-Baselines3: 1.6.1\nPyTorch: 1.12.1+cu113\nGPU Enabled: False\nNumpy: 1.21.6\nGym: 0.20.0\n')


In [ ]:
# Ensure deterministic behavior
torch.backends.cudnn.deterministic = True
random.seed(0)
torch.manual_seed(0)
torch.cuda.manual_seed_all(0)

## Load ELVIS YAML config file
Section where the EVs arrival simulation parameters are loaded through the Yaml config file from the 'data/config_builder/' folder.

In [ ]:
#Loading paths for input data
current_folder = ''
VPP_training_data_input_path = current_folder + 'data/data_training/environment_table/' + 'Environment_data_2019.csv'
VPP_testing_data_input_path = current_folder + 'data/data_testing/environment_table/' + 'Environment_data_2020.csv'
VPP_validating_data_input_path = current_folder + 'data/data_validating/environment_table/' + 'Environment_data_2018.csv'
elvis_input_folder = current_folder + 'data/config_builder/'

#case = 'wohnblock_household_simulation_adaptive.yaml' #(loaded by default, 20 EVs arrivals per week with 50% average battery)

#Try different simulation parameters, uncomment below
#case = 'wohnblock_household_simulation_adaptive_10.yaml' #(10 EVs arrivals per week with 50% average battery) 
#case = 'wohnblock_household_simulation_adaptive_15.yaml' #(15 EVs arrivals per week with 50% average battery)
case = 'wohnblock_household_simulation_adaptive_25.yaml' #(25 EVs arrivals per week with 50% average battery) 
#case = 'wohnblock_household_simulation_adaptive_30.yaml' #(30 EVs arrivals per week with 50% average battery) 
#case = 'wohnblock_household_simulation_adaptive_35.yaml' #(35 EVs arrivals per week with 50% average battery) 

with open(elvis_input_folder + case, 'r') as file:
    yaml_str = yaml.full_load(file)

elvis_config_file = ScenarioConfig.from_yaml(yaml_str)
VPP_config_file = VPP_Scenario_config(yaml_str)

print(elvis_config_file)
print(VPP_config_file)

Vehicle types: <generator object ScenarioConfig.__str__.<locals>.<genexpr> at 0x7f8c2202a950>Mean parking time: 23.99
Std deviation of parking time: 1
Mean value of the SOC distribution: 0.5
Std deviation of the SOC distribution: 0.1
Max parking time: 24
Number of charging events per week: 25
Vehicles are disconnected only depending on their parking time
Queue length: 0
Opening hours: None
Scheduling policy: Uncontrolled

{'start_date': '2022-01-01T00:00:00', 'end_date': '2023-01-01T00:00:00', 'resolution': '0:15:00', 'num_households': 4, 'solar_power': 16, 'wind_power': 12, 'EV_types': [{'battery': {'capacity': 100, 'efficiency': 1, 'max_charge_power': 150, 'min_charge_power': 0}, 'brand': 'Tesla', 'model': 'Model S', 'probability': 1}], 'charging_stations_n': 4, 'EVs_n': 25, 'EVs_n_max': 1305, 'mean_park': 23.99, 'std_deviation_park': 1, 'EVs_mean_soc': 50.0, 'EVs_std_deviation_soc': 10.0, 'EV_load_max': 44, 'EV_load_rated': 14.8, 'EV_load_min': 1, 'houseRWload_max': 10, 'av_max_ener

In [ ]:
#TESTING Environment initialization
env = VPPEnv(VPP_testing_data_input_path, elvis_config_file, VPP_config_file)
env.plot_VPP_input_data()

Output hidden; open in https://colab.research.google.com to view.

In [ ]:
env.plot_ELVIS_data()

In [ ]:
#Function to check custom environment and output additional warnings if needed
check_env(env)
env.plot_reward_functions()

- ELVIS.Simulation (Av.EV_SOC=  50.0 %):
 Sum_Energy=kWh  26510.94 , over-consume=kWh  43063.72 , under-consume=kWh  16552.78 , Total_cost=€  994.79 , overcost=€  1490.9 , Av.EV_en_left=kWh  100.0 , Charging_events=  1304 
- Exp.VPP_goals: Energy_consumed=kWh 0, Av.load=kW 0, Std.load=kW 0, Total_cost=€ 0 , Av.EV_en_left=kWh  70.06
Simulating VPP....


### VPP Simulation test with random actions [no model loaded]

In [ ]:
episodes = 1
for episode in range(1, episodes+1):
    state = env.reset()
    done = False
    score = 0
    while not done:
        action_masks = get_action_masks(env)
        action = env.action_space.sample()
        
        n_state, reward, done, info = env.step(action)
        score+=reward
    print('Episode:{} Score:{}'.format(episode, score))

VPP_table = env.VPP_table
env.plot_VPP_energies()

Output hidden; open in https://colab.research.google.com to view.

In [ ]:
env.plot_Elvis_results()

Output hidden; open in https://colab.research.google.com to view.

In [ ]:
env.plot_VPP_results()

Output hidden; open in https://colab.research.google.com to view.

In [ ]:
env.plot_VPP_Elvis_comparison()

In [ ]:
env.plot_rewards_results()

Output hidden; open in https://colab.research.google.com to view.

In [ ]:
env.plot_rewards_stats()

In [ ]:
env.plot_EVs_kpi()

In [ ]:
env.plot_actions_kpi()

In [ ]:
env.plot_load_kpi()

In [ ]:
env.plot_yearly_load_log()

Output hidden; open in https://colab.research.google.com to view.

In [ ]:
## Wandb login to load models
#In Colab, uncomment below:
# %env "WANDB_DISABLE_CODE" True
# %env "WANDB_NOTEBOOK_NAME" "VPP_simulator.ipynb"
# os.environ['WANDB_NOTEBOOK_NAME'] = 'VPP_simulator.ipynb'
#wandb.login(relogin=True)

#In local notebook, uncomment below:
#your_wandb_login_code = 0123456789abcdefghijklmnopqrstwxyzàèìòù0 #example length
#!wandb login {your_wandb_login_code}

In [ ]:
#Loading training model, from local directory or from wandb previous trainings
RecurrentPPO_path = "trained_models/RecurrentPPO_models/model_RecurrentPPO_"

#model_id = "s37o8q0n"
model_id = "333ckz0i"
model = RecurrentPPO.load(RecurrentPPO_path + model_id, env=env)

# run_id_restore = "2y2dqvyn"
# model = wandb.restore(f'model_{run_id_restore}.zip', run_path=f"francesco_maldonato/RL_VPP_Thesis/{run_id_restore}")

Wrapping the env with a `Monitor` wrapper
Wrapping the env in a DummyVecEnv.


/usr/local/lib/python3.7/dist-packages/stable_baselines3/common/save_util.py:169: UserWarning:

Could not deserialize object _last_lstm_states. Consider using `custom_objects` argument to replace this object.



## Testing dataset VPP Simulation using the loaded trained model

In [ ]:
#TEST Model
episodes = 1
for episode in range(1, episodes+1):
    obs = env.reset()
    done = False
    score = 0
    # cell and hidden state of the LSTM
    lstm_states = None
    num_envs = 1
    # Episode start signals are used to reset the lstm states
    episode_starts = np.ones((num_envs,), dtype=bool)
    while not done:
        #env.render()
        action_masks = get_action_masks(env)
        action, lstm_states = model.predict(obs, state=lstm_states, episode_start=episode_starts, deterministic=True) #Now using our trained model with deterministic prediction [should improve performances]
        env.lstm_state = lstm_states
        obs, reward, done, info = env.step(action)
        episode_starts = done
        score+=reward
    print('Episode:{} Score:{}'.format(episode, score))

#Save the VPP table
VPP_table = env.save_VPP_table(save_path='data/environment_optimized_output/VPP_table.csv')

- ELVIS.Simulation (Av.EV_SOC=  50.0 %):
 Sum_Energy=kWh  26462.31 , over-consume=kWh  43316.35 , under-consume=kWh  16854.04 , Total_cost=€  1053.82 , overcost=€  1542.53 , Av.EV_en_left=kWh  100.0 , Charging_events=  1304 
- Exp.VPP_goals: Energy_consumed=kWh 0, Av.load=kW 0, Std.load=kW 0, Total_cost=€ 0 , Av.EV_en_left=kWh  70.06
Simulating VPP....
- VPP.Simulation results
 LOAD_INFO: Sum_Energy=KWh  -3024.2 , over-consume=KWh  1571.03 , under-consume=KWh  4595.23 , Total_cost=€  -71.44 , Overcost=€  59.24 
 EV_INFO: Av.EV_energy_leaving=kWh  64.16 , Std.EV_energy_leaving=kWh  24.23 , EV_departures =  1307 , EV_queue_left =  0
SCORE:  Cumulative_reward= 440100.06 - Step_rewars (load_t= 403384.69, EVs_energy_t= 7802.54)
 - Final_rewards (EVs_energy= 18236.09, Overconsume= -664.03, Underconsume= -1362.16, Overcost= 12702.93)
Episode:1 Score:440100.06186960003


In [ ]:
env.plot_VPP_energies()

Output hidden; open in https://colab.research.google.com to view.

In [ ]:
VPP_table.head(15000)

0          1          2          3  \
time                                                              
2022-01-01 00:00:00  67.808922  47.324799  48.166454  61.339691   
2022-01-01 00:15:00  68.058922  46.776615  47.618271  61.589691   
2022-01-01 00:30:00  68.308922  46.171299  47.012955  61.839691   
2022-01-01 00:45:00  68.558922  45.693668  46.535324  62.089691   
2022-01-01 01:00:00  68.808922  45.178032  46.019688  62.339691   
...                        ...        ...        ...        ...   
2022-06-06 04:45:00  84.632431  71.340698  45.594444  72.171707   
2022-06-06 05:00:00  85.349693  72.057961  46.311707  72.888969   
2022-06-06 05:15:00  86.092888  72.801155  47.054901  73.632164   
2022-06-06 05:30:00  86.846809  73.555077  47.808819  74.386086   
2022-06-06 05:45:00  87.552040  74.260307  48.514053  75.091316   

                                           EVs_id       actions  \
time                                                              
2022-01-01 00:00:00                  [0, 0, 0, 0]  [1, 2, 2, 1]   
2022-01-01 00:15:00  [15390, 15389, 15388, 15391]  [1, 2, 2, 1]   
2022-01-01 00:30:00  [15390, 15389, 15388, 15391]  [1, 2, 2, 1]   
2022-01-01 00:45:00  [15390, 15389, 15388, 15391]  [1, 2, 2, 1]   
2022-01-01 01:00:00  [15390, 15389, 15388, 15391]  [1, 2, 2, 1]   
...                                           ...           ...   
2022-06-06 04:45:00  [15925, 15926, 15927, 15928]  [1, 1, 1, 1]   
2022-06-06 05:00:00  [15925, 15926, 15927, 15928]  [1, 1, 1, 1]   
2022-06-06 05:15:00  [15925, 15926, 15927, 15928]  [1, 1, 1, 1]   
2022-06-06 05:30:00  [15925, 15926, 15927, 15928]  [1, 1, 1, 1]   
2022-06-06 05:45:00  [15925, 15926, 15927, 15928]  [1, 1, 1, 1]   

                                       mask_truth          load  load_reward  \
time                                                                           
2022-01-01 00:00:00  [False, False, False, False]  1.860713e+00         15.0   
2022-01-01 00:15:00    [False, True, True, False] -4.440892e-16         15.0   
2022-01-01 00:30:00    [False, True, True, False]  0.000000e+00         15.0   
2022-01-01 00:45:00    [False, True, True, False]  0.000000e+00         15.0   
2022-01-01 01:00:00    [False, True, True, False]  0.000000e+00         15.0   
...                                           ...           ...          ...   
2022-06-06 04:45:00      [True, True, True, True]  0.000000e+00         15.0   
2022-06-06 05:00:00      [True, True, True, True]  0.000000e+00         15.0   
2022-06-06 05:15:00      [True, True, True, True]  0.000000e+00         15.0   
2022-06-06 05:30:00      [True, True, True, True]  0.000000e+00         15.0   
2022-06-06 05:45:00      [True, True, True, True]  0.000000e+00         15.0   

                     EV_reward  rewards  
time                                     
2022-01-01 00:00:00        0.0     15.0  
2022-01-01 00:15:00        0.0     15.0  
2022-01-01 00:30:00        0.0     15.0  
2022-01-01 00:45:00        0.0     15.0  
2022-01-01 01:00:00        0.0     15.0  
...                        ...      ...  
2022-06-06 04:45:00        0.0     15.0  
2022-06-06 05:00:00        0.0     15.0  
2022-06-06 05:15:00        0.0     15.0  
2022-06-06 05:30:00        0.0     15.0  
2022-06-06 05:45:00        0.0     15.0  

[15000 rows x 11 columns]

In [ ]:
env.plot_Elvis_results()

Output hidden; open in https://colab.research.google.com to view.

In [ ]:
env.plot_VPP_results()

Output hidden; open in https://colab.research.google.com to view.

In [ ]:
env.plot_VPP_Elvis_comparison()

In [ ]:
env.plot_rewards_results()

Output hidden; open in https://colab.research.google.com to view.

In [ ]:
env.plot_rewards_stats()

In [ ]:
env.plot_EVs_kpi()

In [ ]:
env.plot_load_kpi()

In [ ]:
env.plot_yearly_load_log()

Output hidden; open in https://colab.research.google.com to view.

## Validating dataset VPP Simulation using the loaded trained model

In [ ]:
#VALIDATING Environment initialization
env = VPPEnv(VPP_validating_data_input_path, elvis_config_file, VPP_config_file)

Charging event: 16697, Arrival time: 2022-01-01 09:15:00, Parking_time: 23.396006629150058, Leaving_time: 2022-01-02 08:38:45.623865, SOC: 0.5213423443033608, SOC target: 1.0, Connected car: Tesla, Model S 
 ... 
 Charging event: 18000, Arrival time: 2022-12-31 18:30:00, Parking_time: 24, Leaving_time: 2023-01-01 18:30:00, SOC: 0.6232338728609542, SOC target: 1.0, Connected car: Tesla, Model S 

-DATASET: House&RW_energy_sum=kWh  -30085.39 , over-consume=kWh  2136.67 , under-consume=kWh  -32222.06 , Total_cost=€  -1187.15 , overcost=€  113.34
- ELVIS.Simulation (Av.EV_SOC=  50.0 %):
 Sum_Energy=kWh  18844.97 , over-consume=kWh  39186.85 , under-consume=kWh  20341.88 , Total_cost=€  882.28 , overcost=€  1716.77 , Charging_events=  1304 
- Exp.VPP_goals: Energy_consumed=kWh 0, Av.load=kW 0, Std.load=kW 0, Total_cost=€ 0 , Av.EV_en_left=kWh  74.71


In [ ]:
#Function to check custom environment and output additional warnings if needed
check_env(env)
plot_VPP_input_data = env.plot_VPP_input_data()
plot_VPP_input_data.show()

Output hidden; open in https://colab.research.google.com to view.

In [ ]:
#model = PPO.load(PPO_path + model_run_ID, env = env)
model = RecurrentPPO.load(RecurrentPPO_path + model_id, env=env)

Wrapping the env with a `Monitor` wrapper
Wrapping the env in a DummyVecEnv.


/usr/local/lib/python3.7/dist-packages/stable_baselines3/common/save_util.py:169: UserWarning:

Could not deserialize object _last_lstm_states. Consider using `custom_objects` argument to replace this object.



In [ ]:
#TEST Model
episodes = 1
for episode in range(1, episodes+1):
    obs = env.reset()
    done = False
    score = 0
    # cell and hidden state of the LSTM
    lstm_states = None
    num_envs = 1
    # Episode start signals are used to reset the lstm states
    episode_starts = np.ones((num_envs,), dtype=bool)
    while not done:
        #env.render()
        action_masks = get_action_masks(env)
        action, lstm_states = model.predict(obs, state=lstm_states, episode_start=episode_starts, deterministic=True) #Now using our trained model with deterministic prediction [should improve performances]
        env.lstm_state = lstm_states
        obs, reward, done, info = env.step(action)
        episode_starts = done
        score+=reward
    print('Episode:{} Score:{}'.format(episode, score))

VPP_table = env.VPP_table
#print(env.lstm_states_list)

- ELVIS.Simulation (Av.EV_SOC=  50.0 %):
 Sum_Energy=kWh  18121.92 , over-consume=kWh  38210.12 , under-consume=kWh  20088.2 , Total_cost=€  849.13 , overcost=€  1669.76 , Av.EV_en_left=kWh  100.0 , Charging_events=  1304 
- Exp.VPP_goals: Energy_consumed=kWh 0, Av.load=kW 0, Std.load=kW 0, Total_cost=€ 0 , Av.EV_en_left=kWh  74.71
Simulating VPP....
- VPP.Simulation results
 LOAD_INFO: Sum_Energy=KWh  -4329.58 , over-consume=KWh  941.27 , under-consume=KWh  5270.85 , Total_cost=€  -161.56 , Overcost=€  41.63 
 EV_INFO: Av.EV_energy_leaving=kWh  70.41 , Std.EV_energy_leaving=kWh  23.26 , EV_departures =  1302 , EV_queue_left =  0
SCORE:  Cumulative_reward= 470890.02 - Step_rewars (load_t= 398149.74, EVs_energy_t= 35790.18)
 - Final_rewards (EVs_energy= 23045.5, Overconsume= -189.15, Underconsume= -1169.73, Overcost= 15263.47)
Episode:1 Score:470890.01988631906


In [ ]:
env.plot_VPP_energies()

Output hidden; open in https://colab.research.google.com to view.

In [ ]:
VPP_table.head(15000)

0          1          2          3  \
time                                                              
2022-01-01 00:00:00   0.000000   0.000000   0.000000   0.000000   
2022-01-01 00:15:00   0.000000   0.000000   0.000000   0.000000   
2022-01-01 00:30:00   0.000000   0.000000   0.000000   0.000000   
2022-01-01 00:45:00   0.000000   0.000000   0.000000   0.000000   
2022-01-01 01:00:00   0.000000   0.000000   0.000000   0.000000   
...                        ...        ...        ...        ...   
2022-06-06 04:45:00  79.960091  48.079144  96.071106  63.684994   
2022-06-06 05:00:00  80.797562  48.916615  96.908577  64.522469   
2022-06-06 05:15:00  81.654640  49.773689  97.765656  65.379547   
2022-06-06 05:30:00  82.528023  50.647068  98.639038  66.252930   
2022-06-06 05:45:00  83.369133  51.488182  99.480148  67.094040   

                                           EVs_id       actions  \
time                                                              
2022-01-01 00:00:00                  [0, 0, 0, 0]  [2, 1, 1, 0]   
2022-01-01 00:15:00                  [0, 0, 0, 0]  [2, 1, 1, 0]   
2022-01-01 00:30:00                  [0, 0, 0, 0]  [2, 1, 1, 0]   
2022-01-01 00:45:00                  [0, 0, 0, 0]  [2, 1, 1, 0]   
2022-01-01 01:00:00                  [0, 0, 0, 0]  [2, 0, 1, 0]   
...                                           ...           ...   
2022-06-06 04:45:00  [19859, 19862, 19860, 19861]  [1, 1, 1, 1]   
2022-06-06 05:00:00  [19859, 19862, 19860, 19861]  [1, 1, 1, 1]   
2022-06-06 05:15:00  [19859, 19862, 19860, 19861]  [1, 1, 1, 1]   
2022-06-06 05:30:00  [19859, 19862, 19860, 19861]  [1, 1, 1, 1]   
2022-06-06 05:45:00  [19859, 19862, 19860, 19861]  [1, 2, 1, 1]   

                                      mask_truth      load  load_reward  \
time                                                                      
2022-01-01 00:00:00  [False, False, False, True] -3.997362    -4.568181   
2022-01-01 00:15:00  [False, False, False, True] -3.740908    -5.396378   
2022-01-01 00:30:00  [False, False, False, True] -4.436016    -4.154519   
2022-01-01 00:45:00  [False, False, False, True] -3.492711    -5.500692   
2022-01-01 01:00:00   [False, True, False, True] -4.550761    -5.258359   
...                                          ...       ...          ...   
2022-06-06 04:45:00    [True, True, False, True]  0.000000    15.000000   
2022-06-06 05:00:00    [True, True, False, True]  0.000000    15.000000   
2022-06-06 05:15:00    [True, True, False, True]  0.000000    15.000000   
2022-06-06 05:30:00    [True, True, False, True]  0.000000    15.000000   
2022-06-06 05:45:00   [True, False, False, True]  0.000000    -3.443926   

                     EV_reward    rewards  
time                                       
2022-01-01 00:00:00        0.0  -4.568181  
2022-01-01 00:15:00        0.0  -5.396378  
2022-01-01 00:30:00        0.0  -4.154519  
2022-01-01 00:45:00        0.0  -5.500692  
2022-01-01 01:00:00        0.0  -5.258359  
...                        ...        ...  
2022-06-06 04:45:00        0.0  15.000000  
2022-06-06 05:00:00        0.0  15.000000  
2022-06-06 05:15:00        0.0  15.000000  
2022-06-06 05:30:00        0.0  15.000000  
2022-06-06 05:45:00        0.0  -3.443926  

[15000 rows x 11 columns]

In [ ]:
env.plot_VPP_results()


Output hidden; open in https://colab.research.google.com to view.

In [ ]:
env.plot_VPP_Elvis_comparison()

In [ ]:
env.plot_rewards_results()

Output hidden; open in https://colab.research.google.com to view.

In [ ]:
env.plot_rewards_stats()

In [ ]:
env.plot_EVs_kpi()

In [ ]:
env.plot_load_kpi()

In [ ]:
env.plot_yearly_load_log()

Output hidden; open in https://colab.research.google.com to view.

## Training dataset VPP Simulation using the loaded trained model

In [ ]:
#TRAINING Environment initialization
env = VPPEnv(VPP_training_data_input_path, elvis_config_file, VPP_config_file)

Charging event: 20609, Arrival time: 2022-01-01 15:45:00, Parking_time: 24, Leaving_time: 2022-01-02 15:45:00, SOC: 0.6398709350034594, SOC target: 1.0, Connected car: Tesla, Model S 
 ... 
 Charging event: 21912, Arrival time: 2022-12-31 18:45:00, Parking_time: 23.96456642652541, Leaving_time: 2023-01-01 18:42:52.439135, SOC: 0.4428101087323425, SOC target: 1.0, Connected car: Tesla, Model S 

-DATASET: House&RW_energy_sum=kWh  -34117.7 , over-consume=kWh  1556.25 , under-consume=kWh  -35673.95 , Total_cost=€  -1196.64 , overcost=€  97.86
- ELVIS.Simulation (Av.EV_SOC=  50.0 %):
 Sum_Energy=kWh  13303.51 , over-consume=kWh  35170.34 , under-consume=kWh  21866.83 , Total_cost=€  662.25 , overcost=€  1466.52 , Charging_events=  1304 
- Exp.VPP_goals: Energy_consumed=kWh 0, Av.load=kW 0, Std.load=kW 0, Total_cost=€ 0 , Av.EV_en_left=kWh  77.36


In [ ]:
#Function to check custom environment and output additional warnings if needed
check_env(env)
plot_VPP_input_data = env.plot_VPP_input_data()
plot_VPP_input_data.show()

Output hidden; open in https://colab.research.google.com to view.

In [ ]:
#model = PPO.load(PPO_path + model_run_ID, env = env)
model = RecurrentPPO.load(RecurrentPPO_path + model_id, env=env)

Wrapping the env with a `Monitor` wrapper
Wrapping the env in a DummyVecEnv.


/usr/local/lib/python3.7/dist-packages/stable_baselines3/common/save_util.py:169: UserWarning:

Could not deserialize object _last_lstm_states. Consider using `custom_objects` argument to replace this object.



In [ ]:
#TEST Model
episodes = 1
for episode in range(1, episodes+1):
    obs = env.reset()
    done = False
    score = 0
    # cell and hidden state of the LSTM
    lstm_states = None
    num_envs = 1
    # Episode start signals are used to reset the lstm states
    episode_starts = np.ones((num_envs,), dtype=bool)
    while not done:
        #env.render()
        action_masks = get_action_masks(env)
        action, lstm_states = model.predict(obs, state=lstm_states, episode_start=episode_starts, deterministic=True) #Now using our trained model with deterministic prediction [should improve performances]
        env.lstm_state = lstm_states
        obs, reward, done, info = env.step(action)
        episode_starts = done
        score+=reward
    print('Episode:{} Score:{}'.format(episode, score))

VPP_table = env.VPP_table
#print(env.lstm_states_list)

- ELVIS.Simulation (Av.EV_SOC=  50.0 %):
 Sum_Energy=kWh  14375.81 , over-consume=kWh  37190.34 , under-consume=kWh  22814.53 , Total_cost=€  726.95 , overcost=€  1555.75 , Av.EV_en_left=kWh  100.0 , Charging_events=  1304 
- Exp.VPP_goals: Energy_consumed=kWh 0, Av.load=kW 0, Std.load=kW 0, Total_cost=€ 0 , Av.EV_en_left=kWh  77.36
Simulating VPP....
- VPP.Simulation results
 LOAD_INFO: Sum_Energy=KWh  -6417.36 , over-consume=KWh  780.21 , under-consume=KWh  7197.57 , Total_cost=€  -227.02 , Overcost=€  32.47 
 EV_INFO: Av.EV_energy_leaving=kWh  71.56 , Std.EV_energy_leaving=kWh  23.38 , EV_departures =  1299 , EV_queue_left =  1
SCORE:  Cumulative_reward= 460068.2 - Step_rewars (load_t= 385473.28, EVs_energy_t= 39244.76)
 - Final_rewards (EVs_energy= 21520.94, Overconsume= -39.96, Underconsume= -2165.29, Overcost= 16034.47)
Episode:1 Score:460068.20320125687


In [ ]:
env.plot_VPP_energies()

Output hidden; open in https://colab.research.google.com to view.

In [ ]:
VPP_table.head(14995)

0          1          2          3  \
time                                                              
2022-01-01 00:00:00   0.000000   0.000000   0.000000   0.000000   
2022-01-01 00:15:00   0.000000   0.000000   0.000000   0.000000   
2022-01-01 00:30:00   0.000000   0.000000   0.000000   0.000000   
2022-01-01 00:45:00   0.000000   0.000000   0.000000   0.000000   
2022-01-01 01:00:00   0.000000   0.000000   0.000000   0.000000   
...                        ...        ...        ...        ...   
2022-06-06 03:30:00  76.627472  77.173752  68.182381  55.833046   
2022-06-06 03:45:00  77.446167  76.923752  67.932381  56.651741   
2022-06-06 04:00:00  78.454712  76.673752  67.682381  57.660286   
2022-06-06 04:15:00  79.059723  76.423752  68.287392  58.265301   
2022-06-06 04:30:00  79.641182  76.173752  68.868851  58.846764   

                                           EVs_id       actions  \
time                                                              
2022-01-01 00:00:00                  [0, 0, 0, 0]  [2, 1, 1, 0]   
2022-01-01 00:15:00                  [0, 0, 0, 0]  [2, 1, 1, 0]   
2022-01-01 00:30:00                  [0, 0, 0, 0]  [2, 1, 1, 0]   
2022-01-01 00:45:00                  [0, 0, 0, 0]  [2, 1, 1, 0]   
2022-01-01 01:00:00                  [0, 0, 0, 0]  [2, 0, 1, 0]   
...                                           ...           ...   
2022-06-06 03:30:00  [23767, 23765, 23766, 23768]  [1, 2, 2, 1]   
2022-06-06 03:45:00  [23767, 23765, 23766, 23768]  [1, 2, 2, 1]   
2022-06-06 04:00:00  [23767, 23765, 23766, 23768]  [1, 2, 1, 1]   
2022-06-06 04:15:00  [23767, 23765, 23766, 23768]  [1, 2, 1, 1]   
2022-06-06 04:30:00  [23767, 23765, 23766, 23768]  [1, 2, 1, 1]   

                                      mask_truth      load  load_reward  \
time                                                                      
2022-01-01 00:00:00  [False, False, False, True] -3.239086    -2.971454   
2022-01-01 00:15:00  [False, False, False, True] -2.782873    -4.085185   
2022-01-01 00:30:00  [False, False, False, True] -3.451111    -4.940316   
2022-01-01 00:45:00  [False, False, False, True] -3.964190    -6.814715   
2022-01-01 01:00:00   [False, True, False, True] -5.996187    -6.910563   
...                                          ...       ...          ...   
2022-06-06 03:30:00   [True, False, False, True]  0.000000    15.000000   
2022-06-06 03:45:00   [True, False, False, True]  0.000000    15.000000   
2022-06-06 04:00:00    [True, False, True, True]  0.000000    15.000000   
2022-06-06 04:15:00    [True, False, True, True]  0.000000    15.000000   
2022-06-06 04:30:00    [True, False, True, True]  0.000000    15.000000   

                     EV_reward    rewards  
time                                       
2022-01-01 00:00:00        0.0  -2.971454  
2022-01-01 00:15:00        0.0  -4.085185  
2022-01-01 00:30:00        0.0  -4.940316  
2022-01-01 00:45:00        0.0  -6.814715  
2022-01-01 01:00:00        0.0  -6.910563  
...                        ...        ...  
2022-06-06 03:30:00        0.0  15.000000  
2022-06-06 03:45:00        0.0  15.000000  
2022-06-06 04:00:00        0.0  15.000000  
2022-06-06 04:15:00        0.0  15.000000  
2022-06-06 04:30:00        0.0  15.000000  

[14995 rows x 11 columns]

In [ ]:
env.plot_VPP_results()

Output hidden; open in https://colab.research.google.com to view.

In [ ]:
env.plot_VPP_Elvis_comparison()

In [ ]:
env.plot_rewards_results()

Output hidden; open in https://colab.research.google.com to view.

In [ ]:
env.plot_rewards_stats()

In [ ]:
env.plot_EVs_kpi()

In [ ]:
env.plot_actions_kpi()

In [ ]:
env.plot_load_kpi()

In [ ]:
env.plot_yearly_load_log()

Output hidden; open in https://colab.research.google.com to view.

In [ ]:
#env.close()